<a href="https://colab.research.google.com/github/ziggymoens/HackTheFuture2020/blob/main/Hack_The_Future.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#%reset

In [ ]:
!pip install translators
import json
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.sequence import pad_sequences
import pandas as pd
from keras.wrappers.scikit_learn import KerasClassifier
from tensorflow.keras.initializers import Constant
from tensorflow.keras.layers import Embedding
from tensorflow.keras import layers
import numpy as np
from tensorflow.keras.preprocessing.text import Tokenizer
import translators as ts
from multiprocessing import Pool
from tqdm import *

In [ ]:
# Load datasets into variables

def load_jsonl(input_path) -> list:
    """
    Read list of objects from a JSON lines file.
    """
    data = []
    with open(input_path, 'r', encoding='utf-8') as f:
        for line in f:
            data.append(json.loads(line.rstrip('\n|\r')))
    print('Loaded {} records from {}'.format(len(data), input_path))
    return data

data_comments = load_jsonl("/content/data/comments.gold.jsonl")
data_titles = load_jsonl("/content/data/the_two_genres.titles.gold.jsonl")
data_reddit = load_jsonl("/content/data/reddit2020.htf.gold.jsonl")

Loaded 1912 records from /content/data/comments.gold.jsonl
Loaded 1351 records from /content/data/the_two_genres.titles.gold.jsonl
Loaded 1350 records from /content/data/reddit2020.htf.gold.jsonl


In [ ]:
titles_text = []
titles_cat = []
comments_text = []
comments_boolean = [] 
for d in data_comments:
  comments_text.append(d.get("body").get("text").lower())
  comments_boolean.append(d.get("is_angry"))

for d in data_titles:
  titles_text.append(d.get("title").get("text").lower())
  titles_cat.append(d.get("cat"))

print(titles_text)
print(titles_cat)
print(comments_text)
print(comments_boolean)


['ais from ai dungeon 2 to sexy to funny and one based wholly on reddit!', 'question about a lotr box set', 'how to see current hardware being used right now?', '[no spoilers] i am retarded and i also think season 8 is good. ama!', 'compiling a functional language using c++, part 9 - garbage collection', '[no spoilers] you know nothing, jon snow', 'margaery when the high sparrow or septa unella walks in', 'html string to pdf for react app', 'do you want to learn how to build android games in java?', 'funderal of aragorn by rin [gif by me]', 'bid farwell to a very old friend.', 'how to compare two strings using the java string comparetostring() or comparetoignorecase() methods', "hi everyone, i'm a 15 year old gamedev. i just released my new devlog for my upcoming 3d game, so if you could check it out that would mean a lot :)", 'because the film of "the silmarillion" will never come. da da to peter jackson from others', "as powerful as possible - about early lisp history and major ides 

In [ ]:
def encode(text):
  encoder = LabelEncoder()
  encoder.fit(text)
  return encoder.transform(text)

In [ ]:
# Conver output text from strings or booleans to 0 or 1

# False/not angry = 0 and True/angry = 1
y_train_comments = encode(comments_boolean)
print(comments_boolean)
print(y_train_comments)

# fantasy = 0 en programming = 1
y_train_titles = encode(titles_cat)
print(titles_cat)
print(y_train_titles)

[False, False, True, True, False, True, False, True, False, False, True, True, True, True, True, False, True, False, True, False, True, False, True, True, True, False, False, False, True, True, True, False, False, False, True, False, True, True, True, False, False, False, False, False, True, False, False, True, True, True, False, False, False, True, False, False, False, False, True, True, True, False, False, True, True, False, True, True, False, False, True, True, True, False, True, False, True, False, False, False, False, False, False, False, True, True, True, False, True, True, True, True, False, False, False, False, True, False, False, False, True, True, True, False, True, False, False, False, True, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, False, True, False, True, False, False, True, False, False, True, True, False, False, False, True, True, True, True, True, True, True, False, True, True, True, True, True, Tr

In [ ]:
def translateBack(text, language):
  t1 = ts.google(text, "en", language)
  return ts.google(t1, language, "en")

In [ ]:
# for (idx, text) in enumerate(titles_text):
#   tb = translateBack(text, "es")
#   if titles_text[idx] != tb:
#     titles_text.append(tb)
#     y_train_titles = np.append(y_train_titles, y_train_titles[idx])
#     print(idx)
#   print(idx)
#   if idx == 50:
#     break



In [ ]:
tokenizer_comments = Tokenizer()
raw_comments_text = comments_text
tokenizer_comments.fit_on_texts(raw_comments_text)
train_sequences_comments = tokenizer_comments.texts_to_sequences(raw_comments_text) #Converting text to a vector of word indexes
word_index_comments = tokenizer_comments.word_index
print('comment_titles - Found %s unique tokens.' % len(word_index_comments))
print('comment_titles - 1st token-id sequnce', train_sequences_comments[0])
print(tokenizer_comments.get_config())

tokenizer_titles = Tokenizer()
raw_titles_text = titles_text
tokenizer_titles.fit_on_texts(raw_titles_text)
train_sequences_titles = tokenizer_titles.texts_to_sequences(raw_titles_text) #Converting text to a vector of word indexes
word_index_titles = tokenizer_titles.word_index
print('comment_titles - Found %s unique tokens.' % len(word_index_titles))
print('comment_titles - 1st token-id sequnce', train_sequences_titles[0])

comment_titles - Found 7619 unique tokens.
comment_titles - 1st token-id sequnce [399, 2988, 6, 1867, 39, 36, 205, 1868, 6, 60, 110, 1869, 158]
{'num_words': None, 'filters': '!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n', 'lower': True, 'split': ' ', 'char_level': False, 'oov_token': None, 'document_count': 1912, 'word_counts': '{"dude": 14, "miz": 1, "and": 900, "mrs": 2, "can": 145, "get": 168, "those": 29, "numbers": 2, "it\'s": 94, "way": 54, "cheaper": 2, "lol": 36, "well": 55, "they": 156, "don\'t": 109, "really": 72, "have": 247, "any": 38, "singles": 1, "men": 7, "that": 446, "could": 34, "feed": 2, "to": 915, "ruas": 1, "i": 1049, "know": 92, "of": 643, "it": 481, "used": 20, "be": 231, "ruff": 1, "but": 234, "not": 242, "anymore": 14, "if": 177, "anyone": 19, "a": 1201, "good": 89, "match": 5, "out": 96, "kushida": 1, "suck": 78, "my": 307, "dick": 66, "assure": 1, "you": 1556, "semen": 1, "is": 527, "considered": 2, "wegetarian": 1, "will": 136, "please": 48, "swallow": 1, "thank":

In [ ]:
d_comments = {"raw_comments_text": comments_text, "train_sequence": train_sequences_comments}
df_comments = pd.DataFrame(d_comments)
df_comments.head()# updata df_text

raw_comments_text                                     train_sequence
0  dude miz and mrs can get those numbers and it'...  [399, 2988, 6, 1867, 39, 36, 205, 1868, 6, 60,...
1  well they don't really have any singles men th...  [108, 38, 51, 83, 21, 144, 2989, 672, 10, 38, ...
2  suck my dick \n\ni assure you, my semen is con...  [76, 17, 93, 4, 2993, 1, 17, 2994, 8, 1871, 29...
3  "\ni know, i have tried to vandalize these pas...  [4, 63, 4, 21, 673, 5, 478, 166, 550, 304, 771...
4  not saying it is but in 30 years it could easi...  [22, 773, 9, 8, 23, 11, 344, 267, 9, 165, 886,...

In [ ]:
d_titles = {"raw_titles_text": titles_text, "train_sequence": train_sequences_titles}
df_titles = pd.DataFrame(d_titles)
df_titles.head()# updata df_text

raw_titles_text                                     train_sequence
0  ais from ai dungeon 2 to sexy to funny and one...  [77, 14, 54, 73, 33, 3, 78, 3, 79, 6, 22, 44, ...
1                      question about a lotr box set                         [111, 42, 4, 66, 475, 216]
2  how to see current hardware being used right now?         [12, 3, 126, 870, 871, 193, 392, 329, 153]
3  [no spoilers] i am retarded and i also think s...  [43, 36, 8, 154, 1458, 6, 8, 330, 138, 84, 96,...
4  compiling a functional language using c++, par...      [872, 4, 476, 81, 55, 60, 163, 331, 477, 243]

In [ ]:
# ckeck sequence_length stats
df_comments.train_sequence.apply(lambda x: len(x))
print('sequence_length comments mean: ', df_comments.train_sequence.apply(lambda
x: len(x)).mean())
print('sequence_length comments median: ',
df_comments.train_sequence.apply(lambda x: len(x)).median())


sequence_length comments mean:  23.13807531380753
sequence_length comments median:  15.0


In [ ]:
# ckeck sequence_length stats
df_titles.train_sequence.apply(lambda x: len(x))
print('sequence_length titles mean: ', df_titles.train_sequence.apply(lambda
x: len(x)).mean())
print('sequence_length titles median: ',
df_titles.train_sequence.apply(lambda x: len(x)).median())


sequence_length titles mean:  10.923760177646187
sequence_length titles median:  9.0


In [ ]:
MAX_SEQUENCE_LENGTH_COMMENTS = 17
MAX_SEQUENCE_LENGTH_TITLES = 10

x_train_comments = pad_sequences(train_sequences_comments,maxlen=MAX_SEQUENCE_LENGTH_COMMENTS,padding='pre',truncating='pre',)
print("comments")
print(x_train_comments)
print(len(x_train_comments))
print()

x_train_titles = pad_sequences(train_sequences_titles,maxlen=MAX_SEQUENCE_LENGTH_TITLES,padding='pre',truncating='pre',)
print("titles")
print(x_train_titles)
print(len(x_train_titles))

comments
[[   0    0    0 ...  110 1869  158]
 [2991   23   22 ...  303   60 2992]
 [   4 2993    1 ...  218    1  124]
 ...
 [   0    0    0 ... 1865 7615 2987]
 [7617 2978    1 ...  138   27   10]
 [   0    0    0 ...    2   20  996]]
1912

titles
[[   3   78    3 ...   80   10   65]
 [   0    0    0 ...   66  475  216]
 [   0   12    3 ...  392  329  153]
 ...
 [  44  780   48 ... 1142 3784 3785]
 [   0    0    0 ...    7  128 3786]
 [ 136  124  660 ... 1457    7  209]]
1351


In [ ]:
class TokenAndPositionEmbedding(layers.Layer):
    def __init__(self, maxlen, vocab_size, embed_dim):
        super(TokenAndPositionEmbedding, self).__init__()
        self.token_emb = layers.Embedding(input_dim=vocab_size, output_dim=embed_dim)
        self.pos_emb = layers.Embedding(input_dim=maxlen, output_dim=embed_dim)

    def call(self, x):
        maxlen = tf.shape(x)[-1]
        positions = tf.range(start=0, limit=maxlen, delta=1)
        positions = self.pos_emb(positions)
        x = self.token_emb(x)
        return x + positions

In [ ]:
class MultiHeadSelfAttention(layers.Layer):
    def __init__(self, embed_dim, num_heads=8):
        super(MultiHeadSelfAttention, self).__init__()
        self.embed_dim = embed_dim
        self.num_heads = num_heads
        if embed_dim % num_heads != 0:
            raise ValueError(
                f"embedding dimension = {embed_dim} should be divisible by number of heads = {num_heads}"
            )
        self.projection_dim = embed_dim // num_heads
        self.query_dense = layers.Dense(embed_dim)
        self.key_dense = layers.Dense(embed_dim)
        self.value_dense = layers.Dense(embed_dim)
        self.combine_heads = layers.Dense(embed_dim)

    def attention(self, query, key, value):
        score = tf.matmul(query, key, transpose_b=True)
        dim_key = tf.cast(tf.shape(key)[-1], tf.float32)
        scaled_score = score / tf.math.sqrt(dim_key)
        weights = tf.nn.softmax(scaled_score, axis=-1)
        output = tf.matmul(weights, value)
        return output, weights

    def separate_heads(self, x, batch_size):
        x = tf.reshape(x, (batch_size, -1, self.num_heads, self.projection_dim))
        return tf.transpose(x, perm=[0, 2, 1, 3])

    def call(self, inputs):
        # x.shape = [batch_size, seq_len, embedding_dim]
        batch_size = tf.shape(inputs)[0]
        query = self.query_dense(inputs)  # (batch_size, seq_len, embed_dim)
        key = self.key_dense(inputs)  # (batch_size, seq_len, embed_dim)
        value = self.value_dense(inputs)  # (batch_size, seq_len, embed_dim)
        query = self.separate_heads(
            query, batch_size
        )  # (batch_size, num_heads, seq_len, projection_dim)
        key = self.separate_heads(
            key, batch_size
        )  # (batch_size, num_heads, seq_len, projection_dim)
        value = self.separate_heads(
            value, batch_size
        )  # (batch_size, num_heads, seq_len, projection_dim)
        attention, weights = self.attention(query, key, value)
        attention = tf.transpose(
            attention, perm=[0, 2, 1, 3]
        )  # (batch_size, seq_len, num_heads, projection_dim)
        concat_attention = tf.reshape(
            attention, (batch_size, -1, self.embed_dim)
        )  # (batch_size, seq_len, embed_dim)
        output = self.combine_heads(
            concat_attention
        )  # (batch_size, seq_len, embed_dim)
        return output

In [ ]:
class TransformerBlock(layers.Layer):
    def __init__(self, embed_dim, num_heads, ff_dim, rate=0.1):
        super(TransformerBlock, self).__init__()
        self.att = MultiHeadSelfAttention(embed_dim, num_heads)
        self.ffn = keras.Sequential(
            [layers.Dense(ff_dim, activation="relu"), layers.Dense(embed_dim),]
        )
        self.layernorm1 = layers.LayerNormalization(epsilon=1e-6)
        self.layernorm2 = layers.LayerNormalization(epsilon=1e-6)
        self.dropout1 = layers.Dropout(rate)
        self.dropout2 = layers.Dropout(rate)

    def call(self, inputs, training):
        attn_output = self.att(inputs)
        attn_output = self.dropout1(attn_output, training=training)
        out1 = self.layernorm1(inputs + attn_output)
        ffn_output = self.ffn(out1)
        ffn_output = self.dropout2(ffn_output, training=training)
        return self.layernorm2(out1 + ffn_output)

In [ ]:
embed_dim = 32  # Embedding size for each token
num_heads = 2  # Number of attention heads
ff_dim = 32  # Hidden layer size in feed forward network inside transformer
vocab_size = 20000

In [ ]:
opt = keras.optimizers.Adam(learning_rate=0.0009)

In [ ]:
input_comments = layers.Input(shape=(MAX_SEQUENCE_LENGTH_COMMENTS,))
embedding_layer_comments = TokenAndPositionEmbedding(MAX_SEQUENCE_LENGTH_COMMENTS, vocab_size, embed_dim)
x_comments = embedding_layer_comments(input_comments)
transformer_block1 = TransformerBlock(embed_dim, num_heads, ff_dim)
x_comments = transformer_block1(x_comments)
x_comments = layers.GlobalAveragePooling1D()(x_comments)
x_comments = layers.Dropout(0.4)(x_comments)
x_comments = layers.Dense(32, activation="relu")(x_comments)
x_comments = layers.Dropout(0.3)(x_comments)
x_comments = layers.Dense(32, activation="relu")(x_comments)
outputs_comments = layers.Dense(1, activation="sigmoid")(x_comments)

model_comments = keras.Model(inputs=input_comments, outputs=outputs_comments)
model_comments.compile(loss="binary_crossentropy",optimizer=opt, metrics=["accuracy"])
model_comments.fit(x_train_comments, y_train_comments, batch_size=16, epochs=15)


Epoch 1/15
120/120 [==============================] - 1s 12ms/step - loss: 0.6332 - accuracy: 0.6323
Epoch 2/15
120/120 [==============================] - 1s 12ms/step - loss: 0.2847 - accuracy: 0.8944
Epoch 3/15
120/120 [==============================] - 1s 12ms/step - loss: 0.1092 - accuracy: 0.9660
Epoch 4/15
120/120 [==============================] - 1s 12ms/step - loss: 0.0366 - accuracy: 0.9906
Epoch 5/15
120/120 [==============================] - 1s 12ms/step - loss: 0.0237 - accuracy: 0.9932
Epoch 6/15
120/120 [==============================] - 1s 12ms/step - loss: 0.0124 - accuracy: 0.9979
Epoch 7/15
120/120 [==============================] - 1s 12ms/step - loss: 0.0400 - accuracy: 0.9880
Epoch 8/15
120/120 [==============================] - 1s 12ms/step - loss: 0.0062 - accuracy: 0.9984
Epoch 9/15
120/120 [==============================] - 1s 12ms/step - loss: 0.0024 - accuracy: 0.9995
Epoch 10/15
120/120 [==============================] - 1s 12ms/step - loss: 7.8000e-04 - ac

In [ ]:
inputs_titles = layers.Input(shape=(MAX_SEQUENCE_LENGTH_TITLES,))
embedding_layer_titles = TokenAndPositionEmbedding(MAX_SEQUENCE_LENGTH_TITLES, vocab_size, embed_dim)
x_titles = embedding_layer_titles(inputs_titles)
transformer_block2 = TransformerBlock(embed_dim, num_heads, ff_dim)
x_titles = transformer_block2(x_titles)
x_titles = layers.GlobalAveragePooling1D()(x_titles)
x_titles = layers.Dropout(0.4)(x_titles)
x_titles = layers.Dense(32, activation="relu")(x_titles)
x_titles = layers.Dropout(0.3)(x_titles)
x_titles = layers.Dense(32, activation="relu")(x_titles)
outputs_titles = layers.Dense(1, activation="sigmoid")(x_titles)

model_titles = keras.Model(inputs=inputs_titles, outputs=outputs_titles)
model_titles.compile(loss="binary_crossentropy", optimizer=opt, metrics=["accuracy"])
model_titles.fit(x_train_titles, y_train_titles, batch_size=16, epochs=15)

Epoch 1/15
85/85 [==============================] - 1s 11ms/step - loss: 0.6951 - accuracy: 0.5381
Epoch 2/15
85/85 [==============================] - 1s 12ms/step - loss: 0.3362 - accuracy: 0.8823
Epoch 3/15
85/85 [==============================] - 1s 12ms/step - loss: 0.0762 - accuracy: 0.9837
Epoch 4/15
85/85 [==============================] - 1s 12ms/step - loss: 0.0193 - accuracy: 0.9963
Epoch 5/15
85/85 [==============================] - 1s 12ms/step - loss: 0.0103 - accuracy: 0.9985
Epoch 6/15
85/85 [==============================] - 1s 12ms/step - loss: 0.0021 - accuracy: 1.0000
Epoch 7/15
85/85 [==============================] - 1s 12ms/step - loss: 0.0012 - accuracy: 1.0000
Epoch 8/15
85/85 [==============================] - 1s 12ms/step - loss: 6.7750e-04 - accuracy: 1.0000
Epoch 9/15
85/85 [==============================] - 1s 12ms/step - loss: 6.1657e-04 - accuracy: 1.0000
Epoch 10/15
85/85 [==============================] - 1s 12ms/step - loss: 6.7671e-04 - accuracy: 1.00

In [ ]:
print(data_reddit)

[{'author': 'rilone1', 'title': {'text': 'Flatiron School Software Engineering Graduates'}, 'body': {'text': 'Hey! Can anyone viewing this post who enrolled ... # How to destroy One Code: https://bit.ly/3lVuu59'}, 'comments': [{'text': 'Otorrinolaringología'}, {'text': 'Shit looks crazy'}, {'text': '[removed]'}, {'text': 'WOah FREAK out'}, {'text': "&gt;You are obtuse.\n\nNo. You're being obtuse.\n\n&gt;Was the UK in recession? Yes or no?\n\nThis is the first time you've asked me this.\n\n&gt;You wrote all that just to avoid answering that simple question!\n\nNope. Your original question an d the one I'm trying to stick to was whether Obama was right or wrong to make the statement that Cameron's policies led to a recession. I've given you a collection of reasons why I believe he was and you have rejected them as irrelevant. I don't know why we're still even talking."}]}, {'author': 'Randrewson', 'title': {'text': 'Geom_vline not showing up on ggplot'}, 'body': {'text': 'I created a plo

In [ ]:
reddit_titles = []
reddit_comments = []

for d in data_reddit:
  reddit_titles.append(d.get("title").get("text").lower())
  reddit_comments.append(d.get("comments"))

print(reddit_titles)
print(reddit_comments)

['flatiron school software engineering graduates', 'geom_vline not showing up on ggplot', 'proving algebraic datatypes are “algebraic”', 'international conference on virtual execution environments (vee) 2020 – videos', 'do i need to change my degree plan to become a full stack developer?', 'middle earth | rivendell - music &amp; ambience', 'simpler accessibility rules in ada - feedback requested!', 'lotr youtube content sharing question', 'maybe unpopular opinion about the long night', 'what is this error and how do i get rid of it. i’m new to coding', 'thoughts on the steward and the king chapter?', 'the life of fingolfin | history of middle-earth | lore', 'c# cousins in binary tree [help!]', '(repost) seems about right for this to occur now with everything going on.', 'presenting my latest creation! gollum reads', 'decade after node.js was first announced, javascript and the web platform have evolved, and typescript has changed the way js applications are developed. deno is a new jav

In [ ]:
tokenizer_reddit_titles = tokenizer_titles

raw_reddit_titles = reddit_titles
#tokenizer_reddit_titles.fit_on_texts(raw_reddit_titles)
predict_sequences_reddit_titles = tokenizer_reddit_titles.texts_to_sequences(raw_reddit_titles) #Converting text to a vector of word indexes
word_index_reddit_titles = tokenizer_reddit_titles.word_index
print('Reddit Titles - Found %s unique tokens.' % len(word_index_reddit_titles))
print('Reddit Titles - 1st token-id sequnce', predict_sequences_reddit_titles[0])

Reddit Titles - Found 3786 unique tokens.
Reddit Titles - 1st token-id sequnce [1156, 204, 627]


In [ ]:
x_predict_reddit_titles = pad_sequences(predict_sequences_reddit_titles,maxlen=MAX_SEQUENCE_LENGTH_TITLES,padding='pre',truncating='pre',)
print(x_predict_reddit_titles)

[[   0    0    0 ... 1156  204  627]
 [   0    0    0 ...  708  123   10]
 [   0    0    0 ...    0    0   63]
 ...
 [   0    0    0 ...    4   31   81]
 [   0    0    0 ...  494  526  937]
 [   0    0    0 ... 1886    1  137]]


In [ ]:
reddit_title_predict = model_titles.predict(x_predict_reddit_titles)
print(reddit_title_predict)

[[9.9910665e-01]
 [9.9996173e-01]
 [5.7175756e-04]
 ...
 [9.9999976e-01]
 [9.9999952e-01]
 [6.2230004e-07]]


In [ ]:
reddit_title_predict_programming = []
for i in reddit_title_predict:
  reddit_title_predict_programming.append(i[0])
print(reddit_title_predict_programming)

[0.99910665, 0.99996173, 0.00057175756, 1.0, 1.0, 6.26944e-07, 0.9999995, 0.0014092624, 7.3573807e-07, 0.9999928, 7.6096654e-07, 5.953701e-07, 1.0, 0.10501054, 7.178933e-07, 0.99999946, 0.99999976, 0.9999998, 7.3387054e-07, 0.99999976, 6.6181296e-05, 0.9999999, 1.0, 1.9395989e-06, 0.9999937, 0.99999726, 0.99999964, 6.131373e-07, 6.2053044e-07, 1.1824765e-06, 5.9302806e-07, 1.6660983e-06, 1.0, 1.0, 1.0, 6.371443e-05, 5.730797e-07, 9.794244e-07, 1.0, 0.000361979, 4.327931e-06, 0.99963504, 0.989328, 0.9999999, 0.99999964, 0.13312733, 0.5692202, 1.9539288e-05, 5.773894e-07, 0.0024621487, 1.1883245e-06, 1.0, 8.850286e-07, 2.2602928e-06, 0.99999976, 1.4728521e-05, 6.4689834e-07, 8.888078e-07, 2.050073e-06, 6.163488e-07, 0.0019393563, 1.2803166e-06, 1.0, 6.9307214e-07, 1.7074428e-06, 0.9996517, 0.9994622, 1.0, 1.0, 0.99999964, 0.99999976, 1.0, 1.4192019e-06, 0.0001835525, 0.9991063, 8.883434e-07, 4.585847e-06, 1.0, 0.0054951906, 9.607279e-07, 1.2790741e-06, 0.9999974, 0.9999999, 1.0, 0.599084

In [ ]:
reddit_all_authors = {}
for i in range(len(data_reddit)-1):
  reddit_all_authors[i] = data_reddit[i].get("author")
print(reddit_all_authors)

{0: 'rilone1', 1: 'Randrewson', 2: 'bjzaba', 3: 'mttd', 4: 'SPGOUF', 5: 'healthandreea', 6: 'Fabien_C', 7: 'g0s0_85', 8: 'chelsz02', 9: 'mr-man76', 10: 'Pale_Newt', 11: 'Hayman021', 12: 'bamfdan', 13: 'RxPapers14', 14: 'g0s0_85', 15: 'Cf_Tech', 16: 'newpythoncoder', 17: 'branikita', 18: 'The_Repressions', 19: 'Keemopaul007', 20: 'StonerLoner93', 21: 'marqueedesign', 22: 'MaoStevemao', 23: 'nt10110', 24: 'mttd', 25: 'oilshell', 26: 'durgeshsamariya', 27: 'Kaboom_up3', 28: 'mindfulness-smeagol', 29: 'verdagon', 30: 'Hayman021', 31: 'DARK-LORD-SAURON', 32: 'geeksforgeeks', 33: 'AMisteryMan', 34: 'BrainStormAchievers', 35: 'TimeTurner394', 36: 'Hayman021', 37: 'WorkingPotential5621', 38: 'forzahid1', 39: 'Urgoth-Da', 40: 'themeras', 41: 'mttd', 42: 'jadek77', 43: 'codeforyoungs', 44: 'AlSweigart', 45: 'Noob21213', 46: 'wolffwanderer', 47: 'CompetitivePomelo', 48: 'Hayman021', 49: 'heywadap', 50: 'aFuckinChair', 51: 'chonyyy', 52: 'DopeYeti', 53: 'Sari_Morkos', 54: 'TAOL_Beast', 55: 'xerobl

In [ ]:
#list to dictionary(id, score programming)
title_programming_score = {}

for i in range(0, len(reddit_all_authors)-1):
  title_programming_score[i]= reddit_title_predict_programming[i]
print(title_programming_score)

{0: 0.99910665, 1: 0.99996173, 2: 0.00057175756, 3: 1.0, 4: 1.0, 5: 6.26944e-07, 6: 0.9999995, 7: 0.0014092624, 8: 7.3573807e-07, 9: 0.9999928, 10: 7.6096654e-07, 11: 5.953701e-07, 12: 1.0, 13: 0.10501054, 14: 7.178933e-07, 15: 0.99999946, 16: 0.99999976, 17: 0.9999998, 18: 7.3387054e-07, 19: 0.99999976, 20: 6.6181296e-05, 21: 0.9999999, 22: 1.0, 23: 1.9395989e-06, 24: 0.9999937, 25: 0.99999726, 26: 0.99999964, 27: 6.131373e-07, 28: 6.2053044e-07, 29: 1.1824765e-06, 30: 5.9302806e-07, 31: 1.6660983e-06, 32: 1.0, 33: 1.0, 34: 1.0, 35: 6.371443e-05, 36: 5.730797e-07, 37: 9.794244e-07, 38: 1.0, 39: 0.000361979, 40: 4.327931e-06, 41: 0.99963504, 42: 0.989328, 43: 0.9999999, 44: 0.99999964, 45: 0.13312733, 46: 0.5692202, 47: 1.9539288e-05, 48: 5.773894e-07, 49: 0.0024621487, 50: 1.1883245e-06, 51: 1.0, 52: 8.850286e-07, 53: 2.2602928e-06, 54: 0.99999976, 55: 1.4728521e-05, 56: 6.4689834e-07, 57: 8.888078e-07, 58: 2.050073e-06, 59: 6.163488e-07, 60: 0.0019393563, 61: 1.2803166e-06, 62: 1.0, 

In [ ]:
#new dictionary with best scores of programming
REDDIT_PROGRAMMING_TRESHOLD = 0.5
reddit_titles_programming_treshold={}

for (k,v) in title_programming_score.items():
  if(v > REDDIT_PROGRAMMING_TRESHOLD):
    reddit_titles_programming_treshold[k] = v

print(reddit_titles_programming_treshold)
print(len(reddit_titles_programming_treshold))

{0: 0.99910665, 1: 0.99996173, 3: 1.0, 4: 1.0, 6: 0.9999995, 9: 0.9999928, 12: 1.0, 15: 0.99999946, 16: 0.99999976, 17: 0.9999998, 19: 0.99999976, 21: 0.9999999, 22: 1.0, 24: 0.9999937, 25: 0.99999726, 26: 0.99999964, 32: 1.0, 33: 1.0, 34: 1.0, 38: 1.0, 41: 0.99963504, 42: 0.989328, 43: 0.9999999, 44: 0.99999964, 46: 0.5692202, 51: 1.0, 54: 0.99999976, 62: 1.0, 65: 0.9996517, 66: 0.9994622, 67: 1.0, 68: 1.0, 69: 0.99999964, 70: 0.99999976, 71: 1.0, 74: 0.9991063, 77: 1.0, 81: 0.9999974, 82: 0.9999999, 83: 1.0, 84: 0.5990846, 87: 0.99999946, 88: 1.0, 92: 0.99999344, 95: 0.99787974, 96: 0.98557174, 101: 1.0, 102: 0.9999984, 103: 0.99981475, 104: 1.0, 107: 0.99999917, 108: 0.99995637, 109: 0.99999976, 110: 0.99999976, 111: 0.99999976, 113: 0.99999976, 114: 0.99999917, 115: 0.99999976, 117: 0.9999953, 119: 0.9999999, 120: 0.9995836, 121: 0.9999974, 122: 1.0, 125: 0.9999943, 127: 1.0, 130: 0.9997373, 132: 1.0, 133: 0.99987596, 134: 0.9999996, 135: 0.99999964, 138: 0.9999986, 141: 1.0, 142: 

In [ ]:
USE_PROGRAMMING_TRESHOLD = False

tokenizer_reddit_comments = Tokenizer()

comments = {}

fill_comments_dict_keys = reddit_all_authors.keys()
if USE_PROGRAMMING_TRESHOLD :
   fill_comments_dict_keys = reddit_titles_programming_treshold.keys()


for id in fill_comments_dict_keys:
  temp_comments = data_reddit[id].get("comments")
  comments_list = []
  for comment in temp_comments:
    comments_list.append(comment.get("text"))
  comments[id] = comments_list


print(comments)

{0: ['Otorrinolaringología', 'Shit looks crazy', '[removed]', 'WOah FREAK out', "&gt;You are obtuse.\n\nNo. You're being obtuse.\n\n&gt;Was the UK in recession? Yes or no?\n\nThis is the first time you've asked me this.\n\n&gt;You wrote all that just to avoid answering that simple question!\n\nNope. Your original question an d the one I'm trying to stick to was whether Obama was right or wrong to make the statement that Cameron's policies led to a recession. I've given you a collection of reasons why I believe he was and you have rejected them as irrelevant. I don't know why we're still even talking."], 1: ['Epic post!', "Do not short Tesla. Don't do it. I've managed to save thousands by going against all my instincts and not shorting them. I also don't buy it.", "Jaycie\nIt's not as simple as you put it man! It's not just about some trying to get a reputation! She already is known out there, and read the more detailed one for what I'm trying to get across! FFS! No-one is right deletin

In [ ]:
x_predict_reddit_comments_array = {}

for (id, comments_list) in comments.items():
  tokenizer_reddit_comments = tokenizer_comments
  raw_reddit_comments = comments_list
  #tokenizer_reddit_comments.fit_on_texts(raw_reddit_comments)
  tokenized_sequences_reddit_comments = tokenizer_reddit_comments.texts_to_sequences(raw_reddit_comments) #Converting text to a vector of word indexes
  word_index_reddit_comments = tokenizer_reddit_comments.word_index
  x_predict_comments = pad_sequences(tokenized_sequences_reddit_comments,maxlen=MAX_SEQUENCE_LENGTH_COMMENTS,padding='pre',truncating='pre',)
  x_predict_reddit_comments_array[id] = x_predict_comments

In [ ]:
print(x_predict_reddit_comments_array)

{0: array([[   0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
           0,    0,    0,    0,    0,    0],
       [   0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
           0,    0,    0,   37,  246,  541],
       [   0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
           0,    0,    0,    0,    0,  206],
       [   0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
           0,    0,    0,    0, 1351,   58],
       [  42,   28,    6,    1,   21, 3353,  122,   32, 1745,    4,   51,
          63,   64,  695,  117,   90,  704]], dtype=int32), 1: array([[   0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
           0,    0,    0,    0, 2358,  207],
       [3033,    5,  587, 2088,   74,   77,  978,   35,   17,    6,   22,
         122,    4,   95,   51,  657,    9],
       [  36, 1770, 6612,   44,   54,    8,  114,  437,    9,  705, 1189,
        6779, 3458, 4471, 1223, 7570,  365],
       [   0,    0,    0, 

In [ ]:
predict_sequences_reddit_comments_array = {}

for (id, comments_list) in x_predict_reddit_comments_array.items():
  predict_sequences_reddit_comments_array[id] = model_comments.predict(np.array(comments_list))

In [ ]:
print(predict_sequences_reddit_comments_array)

{0: array([[3.6488427e-07],
       [6.6329085e-07],
       [3.0119077e-07],
       [2.3219936e-06],
       [9.9244809e-01]], dtype=float32), 1: array([[2.6287844e-07],
       [1.2906517e-05],
       [9.9999559e-01],
       [1.0000000e+00],
       [1.9834697e-02]], dtype=float32), 2: array([[1.0256128e-06],
       [3.7056463e-07],
       [1.2912494e-06],
       [3.6488427e-07],
       [6.2706835e-07]], dtype=float32), 3: array([[3.6488427e-07],
       [7.9267051e-07],
       [4.3561698e-07],
       [1.0369694e-06],
       [2.5285934e-07]], dtype=float32), 4: array([[1.        ],
       [1.        ],
       [1.        ],
       [0.00828505],
       [1.        ]], dtype=float32), 5: array([[1.9901640e-06],
       [2.6182204e-01],
       [3.6488427e-07],
       [3.0119077e-07],
       [5.1181951e-06]], dtype=float32), 6: array([[4.0777894e-07],
       [4.0777894e-07],
       [3.0119077e-07],
       [1.8523629e-07],
       [4.0777894e-07]], dtype=float32), 7: array([[2.5621623e-02],
       

In [ ]:
# from array in array => 1 array with all predictions
predict_sequences_reddit_comments = {}

for (id, predictions) in predict_sequences_reddit_comments_array.items():
  temp = []
  for value in predictions:
    temp.append(value[0])
  predict_sequences_reddit_comments[id] = temp

In [ ]:
print(predict_sequences_reddit_comments)

{0: [3.6488427e-07, 6.6329085e-07, 3.0119077e-07, 2.3219936e-06, 0.9924481], 1: [2.6287844e-07, 1.2906517e-05, 0.9999956, 1.0, 0.019834697], 2: [1.0256128e-06, 3.7056463e-07, 1.2912494e-06, 3.6488427e-07, 6.2706835e-07], 3: [3.6488427e-07, 7.926705e-07, 4.3561698e-07, 1.0369694e-06, 2.5285934e-07], 4: [1.0, 1.0, 1.0, 0.008285046, 1.0], 5: [1.990164e-06, 0.26182204, 3.6488427e-07, 3.0119077e-07, 5.118195e-06], 6: [4.0777894e-07, 4.0777894e-07, 3.0119077e-07, 1.8523629e-07, 4.0777894e-07], 7: [0.025621623, 0.0013981462, 0.9619179, 6.493711e-06, 1.9323613e-06], 8: [2.1159875e-07, 0.99999976, 5.750125e-06, 5.919184e-05, 0.03337902], 9: [2.8847907e-07, 3.5538835e-07, 5.9318137e-07, 2.0215438e-07, 3.8855586e-07], 10: [0.9472574, 0.00041669607, 2.48588e-07, 2.7855156e-06, 2.7744085e-07], 11: [8.9446246e-07, 1.2006792e-07, 2.3256958e-07, 4.628556e-07, 1.5839091e-06], 12: [0.044707328, 0.027486235, 2.4565296e-07, 6.1733243e-07, 2.9135478e-07], 13: [1.2692698e-07, 0.006565124, 0.9999897, 0.27698

In [ ]:
prediction_reddit_per_comment = {}

STRATEGY = "MEDIAN"
PREDICTION_ANGRY_TRESHOLD = 0.5

for (id, comment_predictions) in predict_sequences_reddit_comments.items():
  if STRATEGY == "MEAN":
    prediction_reddit_per_comment[id] = np.mean(comment_predictions)
  if STRATEGY == "MEDIAN":
    prediction_reddit_per_comment[id] = np.median(comment_predictions)
  if STRATEGY == "BASED_ON_TOTAL":
    count_angry_comments = 0
    for prediction in comment_predictions:
      if(prediction > PREDICTION_ANGRY_TRESHOLD):
        count_angry_comments += 1
    prediction_reddit_per_comment[id] = count_angry_comments/len(comment_predictions)

In [ ]:
print(prediction_reddit_per_comment)
print(len(prediction_reddit_per_comment))

{0: 6.6329085e-07, 1: 0.019834697, 2: 6.2706835e-07, 3: 4.3561698e-07, 4: 1.0, 5: 1.990164e-06, 6: 4.0777894e-07, 7: 0.0013981462, 8: 5.919184e-05, 9: 3.5538835e-07, 10: 2.7855156e-06, 11: 4.628556e-07, 12: 6.1733243e-07, 13: 0.006565124, 14: 3.0119077e-07, 15: 1.0, 16: 3.6488427e-07, 17: 3.426646e-07, 18: 9.983252e-06, 19: 5.273973e-07, 20: 0.9999996, 21: 4.925123e-07, 22: 6.51642e-07, 23: 3.6488427e-07, 24: 3.0119077e-07, 25: 3.350056e-07, 26: 8.5201054e-07, 27: 3.7188371e-07, 28: 3.6488427e-07, 29: 9.0044074e-07, 30: 1.0138816e-06, 31: 1.0, 32: 0.99999976, 33: 2.7281436e-07, 34: 2.5950504e-07, 35: 0.99689865, 36: 4.420748e-06, 37: 2.4904941e-06, 38: 9.004553e-07, 39: 0.00097242, 40: 2.9197784e-07, 41: 8.178638e-07, 42: 3.7077106e-07, 43: 4.0777894e-07, 44: 1.0, 45: 7.22608e-07, 46: 1.0310301e-06, 47: 0.0014080107, 48: 9.688472e-06, 49: 7.85657e-07, 50: 0.9999936, 51: 0.0011751056, 52: 7.051469e-07, 53: 0.99999976, 54: 4.3785445e-07, 55: 8.428175e-06, 56: 4.736774e-07, 57: 1.0, 58: 2

In [ ]:
prediction_reddit_per_comment_treshold = {}
REDDIT_COMMENT_TRESHOLD = 0.875

for (id, score) in prediction_reddit_per_comment.items():
  if (score >= REDDIT_COMMENT_TRESHOLD):
    prediction_reddit_per_comment_treshold[id]= score

In [ ]:
print(prediction_reddit_per_comment_treshold)
print(len(prediction_reddit_per_comment_treshold))

{4: 1.0, 15: 1.0, 20: 0.9999996, 31: 1.0, 32: 0.99999976, 35: 0.99689865, 44: 1.0, 50: 0.9999936, 53: 0.99999976, 57: 1.0, 67: 0.99999976, 77: 1.0, 78: 0.9999997, 83: 1.0, 88: 0.999994, 90: 1.0, 95: 1.0, 97: 0.9999999, 99: 1.0, 108: 1.0, 116: 0.9999999, 119: 0.9999999, 123: 1.0, 133: 0.999693, 137: 1.0, 157: 0.9999987, 158: 1.0, 167: 0.9999925, 176: 0.99999833, 179: 1.0, 187: 1.0, 197: 0.99999726, 201: 0.99999964, 202: 1.0, 217: 0.9999996, 219: 0.99958134, 228: 0.9999994, 229: 1.0, 231: 1.0, 237: 0.99999917, 243: 1.0, 249: 1.0, 260: 1.0, 261: 1.0, 264: 0.99999774, 304: 0.9999869, 307: 0.99999136, 314: 1.0, 321: 0.99999833, 322: 1.0, 324: 1.0, 326: 0.9338113, 328: 1.0, 347: 1.0, 356: 0.9999994, 365: 0.99920267, 384: 0.9999997, 394: 0.99999756, 405: 1.0, 406: 0.9999957, 411: 0.99999976, 415: 0.9999977, 436: 1.0, 442: 0.9999999, 444: 0.9999969, 449: 0.999999, 452: 0.9999996, 457: 1.0, 460: 0.99999976, 469: 1.0, 471: 1.0, 481: 1.0, 486: 1.0, 493: 1.0, 500: 0.9999994, 507: 0.99998724, 509: 

In [ ]:
result = []

keysTitle = list(reddit_titles_programming_treshold.keys())
keysComments = list(prediction_reddit_per_comment_treshold.keys())

In [ ]:
print(keysTitle)
print(len(keysTitle))
print(keysComments)
print(len(keysComments))

[0, 1, 3, 4, 6, 9, 12, 15, 16, 17, 19, 21, 22, 24, 25, 26, 32, 33, 34, 38, 41, 42, 43, 44, 46, 51, 54, 62, 65, 66, 67, 68, 69, 70, 71, 74, 77, 81, 82, 83, 84, 87, 88, 92, 95, 96, 101, 102, 103, 104, 107, 108, 109, 110, 111, 113, 114, 115, 117, 119, 120, 121, 122, 125, 127, 130, 132, 133, 134, 135, 138, 141, 142, 148, 152, 153, 154, 156, 157, 158, 159, 161, 165, 166, 168, 170, 171, 173, 175, 177, 179, 180, 181, 183, 188, 189, 191, 192, 193, 195, 197, 200, 201, 203, 204, 205, 206, 208, 209, 210, 211, 212, 213, 214, 216, 218, 221, 224, 227, 229, 231, 232, 235, 239, 241, 242, 246, 249, 250, 251, 252, 253, 256, 257, 258, 259, 262, 264, 265, 266, 267, 270, 273, 278, 279, 285, 286, 288, 290, 292, 297, 299, 301, 303, 305, 308, 309, 311, 312, 313, 315, 316, 318, 321, 323, 330, 331, 333, 335, 337, 341, 342, 344, 345, 348, 349, 350, 351, 352, 354, 360, 362, 365, 371, 372, 373, 376, 377, 378, 384, 386, 387, 388, 390, 391, 392, 393, 399, 400, 401, 402, 403, 406, 407, 410, 412, 416, 417, 420, 424, 4

In [ ]:
temp_result = set(keysTitle)&set(keysComments)
result = sorted(temp_result)

In [ ]:
print(result)
print(len(result))

[4, 15, 32, 44, 67, 77, 83, 88, 95, 108, 119, 133, 157, 158, 179, 197, 201, 229, 231, 249, 264, 321, 365, 384, 406, 436, 442, 444, 449, 452, 457, 460, 469, 471, 493, 519, 550, 592, 607, 624, 625, 641, 664, 668, 691, 709, 724, 752, 761, 794, 816, 888, 897, 906, 938, 939, 1022, 1025, 1026, 1046, 1050, 1060, 1062, 1064, 1066, 1091, 1103, 1106, 1115, 1118, 1139, 1144, 1149, 1151, 1153, 1210, 1235, 1240, 1244, 1258, 1274, 1286, 1290, 1341, 1342, 1344]
86


In [ ]:
authnames = []
for id in result:
  authnames.append(reddit_all_authors[id])

In [ ]:
print(authnames)
print(len(authnames))

['SPGOUF', 'Cf_Tech', 'geeksforgeeks', 'AlSweigart', 'anh86', 'harry719', 'DXTJam', 'TheArtofWarPIGEON', 'OhAlrightMang', 'badmight', 'Jesus_Would_Do', 'BestFlatworm', 'gauravghai76', 'gabrielesilinic', 'cutculus', 'L18mvj', 'mttd', 'binarycat64', 'prathyvsh', 'Brightisaac', 'samacct', 'summerinstana', 'bollong', 'basakstuff', 'itsfeykro', 'Academic_Help', 'jshsjsos', 'Toasty0909', 'mttd', 'Academic_Help', 'notimeforarcs', 'HuntieRW', 'Dvdmatsunaga', 'needtobemorecreate', 'JimLessly', 'Wynns', 'N0rthbridge', 'THE_REAL_ODB', 'TheLakeExperience', 'bcsexorg', 'escork', 'decameron77', 'xPusteblume', 'MaoStevemao', 'binarycat64', 'KelyDM', 'torecoverapost', 'mttd', 'alex-manool', 'MonteiroMaravilha', 'PhilosophicalTyrant', 'awwwes', 'walhmr', 'Lolzor', 'BrainStormAchievers', 'Majikarpp', 'Seize_The_Dayx', 'MaoStevemao', 'Drbeen709207', 'Mayurtale', 'Oles_Mironov_Mironov', 'Coopertrooper7', 'Icedcoffeekid', 'srebalaji', 'toselx', 'hackerfoo', 'rockefeller22', 'darmodyjimguy', 'eggplantkiller

In [ ]:
import requests  # remember to install first

identification_endpoint = 'https://brainjar-intern.appspot.com/api/v1/troll_identifier'
header = {'api-key': '18a46c3641257d34a48fd1f74a2689b03810c3ab'}  # TODO: fill in your api-key/authentication token.

users = []  # TODO: Users that you suspect of belonging to the Trolls. List must contain at least 6 *unique* user names.
payload = {'users': authnames}

# send a post requests
r = requests.post(identification_endpoint, headers=header, json=payload)

# print out the status code
print(r.status_code)
# 200 --> New high score
# 418 --> Success, but no new high score
# 400 --> Too soon or improper payload

# Inspect JSON response
print(r.json())

418
{'attempts': 45, 'high_score': 0.8723404255319148, 'message': 'Not high enough. Try something else!', 'score': 0.8654970760233918}
